In [ ]:
from pathlib import Path

import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

DATA = Path("/tmp/Daten_FSP/")  # noqa: S108

# Selbstlernphase: SOEP kennenlernen

Diese Woche lernen Sie die SOEP Daten genauer kennen. Ziel dieses Notebooks ist es, sie an die Datenstruktur heranzuführen. Die behandelten Themen wurden zu Illustrationszwecken gewählt.

Für das SOEP gibt es verschiedene Websites, die Informationen enthalten. Der [SOEP-Companion](http://companion.soep.de/) ist oft eine gute erste Anlaufstelle, um sich einen Überblick zu verschaffen. Außerdem ist es wichtig zu wissen, dass die SOEP Rohdaten aus vielen verschiedenen Datensätzen auf Individuen- oder Haushaltsebene bestehen. Eine Liste der Datensätze finden Sie [hier](https://paneldata.org/soep-core/datasets/).

Wir laden als erstes den Datensatz **pgen**.

In [ ]:
pgen = pd.read_pickle(DATA / "pgen_2019.pkl")  # noqa: S301

Verschaffen Sie sich einen groben Überblick. Welche Variablen enthält dieser Datensatz? Sie können die eben genannten Websites zurate ziehen.

In [ ]:
pgen.columns

Wie Sie sehen sind die Variablennamen oft nicht aussagekräfitg. Schauen wir uns manche Variablen genauer an.

In [ ]:
pgen[["cid", "hid", "pid"]]

Diese Variablen sind essentiell um Informationen aus verschiedenen Datensätzen zu verknüpfen. Finden Sie heraus wofür diese vier Variablen stehen. Sie können dafür [diese Website](https://paneldata.org/soep-core/datasets/pgen/) nutzen. Was ist der Unterschied zwischen `cid` und `hid`?

Wie viele Beobachtungen und Variablen enthält der Datensatz?

In [ ]:
pgen.shape

Wie viele verschiedene (!) Individuen und wie viele verschiedene aktuelle Haushalte sind in diesem Datensatz enthalten?

**Tipp:** Mittels der Methode `nunique()` erhalten Sie die Anzahl an Merkmalsausprägungen, nähere Infos [hier](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.nunique.html).

Welche Variable wird benötigt, um eine Beobachtung zu identifizieren? Erstellen Sie eine
Variable `pgen_sorted`, welche den Datensatz mit entsprechen gesetztem und sortierten
Index enthält.

Als beispielhalte Übungsaufgabe möchten wir die Arbeitszeit von Frauen und Männern
vergleichen. Suchen Sie dafür folgende Spalten heraus.

1. wöchentliche vereinbarte Arbeitszeit
2. wöchentliche tatsächliche Arbeitszeit

Erstellen Sie eine Variable `pgen_arbeit` aus `pgen_sorted`, welche aus dem Datensatz
nur die zwei von Ihnen identifizierten Spalten enthält.

Bennen Sie die beiden Spalten mit der Arbeitszeit um. Dazu können Sie folgende Vorlage
verwenden:

```python
pgen_arbeit = pgen_arbeit.rename(
    columns={
        "Spalte 1": "vereinbarte Arbeitszeit",
        "Spalte 2": "tatsächliche Arbeitszeit"
    }
)
``````

Wenn wir nun versuchen die Überstunden zu berechnen als:

```python
pgen_arbeit["überstunden"] = (
    pgen_arbeit["tatsächliche Arbeitszeit"]
    - pgen_arbeit["vereinbarte Arbeitszeit"]
)
```

resultiert das in einer Fehlermeldung.

Der Grund hierfür ist, dass die Variablen nicht nur angegebene Stunden, sondern auch
verschiedene missing values z.B. `"[-1] keine Angabe"` beinhalten. Schauen Sie auf der
[Website](https://paneldata.org/soep-core/datasets/pgen/pgtatzeit) welche verschiedenen
missings es gibt. Der Einfachheit halber wollen wir hier alle gleich `np.nan` setzten.
Das erlaubt uns den Datentyp zu float (einer Fließkommazahl, die typische Art, reele
Zahlen zu approximieren) zu ändern. Ergänzen Sie den folgenden Code entsprechend.

```python
pgen_arbeit[["tatsächliche Arbeitszeit", "vereinbarte Arbeitszeit"]] = (
    pgen_arbeit[["tatsächliche Arbeitszeit", "vereinbarte Arbeitszeit"]].replace(
        {
            "[-1] keine Angabe": np.nan,
            ...
        }
    )
).astype("float")
```

Sie können sich eine zusammenfassende Statistik der Spalten anschauen:

In [ ]:
pgen_arbeit["vereinbarte Arbeitszeit"].describe()

Nun können wir uns ein Histogramm der beiden Arbeitszeitmaße anschauen.

In [ ]:
pgen_arbeit.plot.hist(
    x=["tatsächliche Arbeitszeit", "vereinbarte Arbeitszeit"],
    histnorm="percent",
    nbins=50,
)

Zuletzt schauen wir uns die Verteilung der Arbeitsstunden nach Geschlecht an.

Die Geschlechtsinformation ist jedoch nicht im **pgen** Datensatz enthalten. Um diese zu erhalten, müssen wir den **pequiv** Datensatz an unseren derzeitigen Datensatz joinen.

In [ ]:
pequiv = pd.read_pickle(DATA / "pequiv_2019.pkl")  # noqa: S301

Suchen Sie mithilfe der [Website](https://paneldata.org/soep-core/datasets/) den
Variablennamen der Geschlechtsvariable im **pequiv** Datensatz. Überschreiben Sie den
Datensatz, sodass er nur die Variablen `pid` und die von Ihnen gefundene Variable
enthält.

Um die beiden Datensätze zu joinen setzen wir wie immer den passenden Index.

In [ ]:
pequiv = pequiv.set_index(["pid"])

In [ ]:
data_merged = pgen_arbeit.join(pequiv)
data_merged

Wir ersetzen wieder die fehlenden Werte und passen den Datentyp an. Hier behalten wir
nur Individuen, die weiblich oder männlich angegeben haben.

In [ ]:
data_merged["geschlecht"] = (
    data_merged["d11102ll"]
    .replace(
        {
            "[2] Female": "weiblich",
            "[1] Male": "maennlich",
        },
    )
    .astype(str)
)
data_merged = data_merged[data_merged["geschlecht"].isin(["weiblich", "maennlich"])]

Erstellen Sie nun ein Histogram, welches die vereinbarte Arbeitszeit beider Geschlechter darstellt. Falls Sie den Output interpretieren möchten, bedenken Sie, dass Individuen, die keiner Erwerbstätigkeit nachgehen, hier nicht enthalten sind.